In [ ]:
# Gerekli temel kurulumu tek satırda yap: ÇALIŞTIRILACAK
!pip uninstall -y numpy tensorflow tensorflow_hub jax jaxlib flax tf-keras xarray opencv-python opencv-contrib-python arviz tensorflow-text ml_dtypes scipy

In [ ]:
# TensorFlow ve TF Hub (uyumlu) ÇALIŞTIRILACAK (BURADA OTURUM YENİDEN BAŞLAT DİYECEK-2 DAKİKA SONRA OTURUMA YENİDEN BAŞLAT DÜĞMESİNE TIKLANACAK)
!pip install tensorflow==2.20.0
!pip install tensorflow_hub==0.16.1

# NumPy ve SciPy
!pip install numpy==1.25.0
!pip install scipy==1.11.3
!pip install ml-dtypes==0.6.0

# JAX
!pip install jax==0.5.3 jaxlib==0.5.3 --no-deps

# Protobuf (TF 2.20 ile uyumlu)
!pip install protobuf==5.28.3

In [ ]:
file_path = f"/content/drive/MyDrive/FL_RESULTS.txt"  #OTURUM YENİDEN BAŞLATILINCA BURADAN ÇALIŞTIRILMAYA BAŞLANACAK
with open(file_path, "w", encoding="utf-8") as f:
    f.write("")

In [ ]:
from google.colab import drive #ÇALIŞTIRILACAK
drive.mount('/content/drive')
import sys
sys.path.append('/content/drive/MyDrive')
from data_loader import load_rsna_data, load_roboflow_data, load_breakhis_data,load_busi_data,load_bcfpp_data
from config import model_handle_map
import kagglehub
from FedCycleTraining import train_fedcycle_model
from modelbuilder import make_nn_model_efficientb0,make_nn_model_efficientb7,make_nn_model_mobileNet, make_nn_model_resnet152, make_nn_model_dense
import time
from tensorflow.keras.callbacks import ModelCheckpoint, CSVLogger, LambdaCallback
from tensorflow.keras.optimizers import AdamW
from tensorflow.keras.metrics import Precision, Recall

Drive already mounted at /content/drive; to attempt to forcibly remount, call drive.mount("/content/drive", force_remount=True).


/usr/local/lib/python3.12/dist-packages/jax/_src/cloud_tpu_init.py:82: UserWarning: Transparent hugepages are not enabled. TPU runtime startup and shutdown time should be significantly improved on TPU v5e and newer. If not already set, you may need to enable transparent hugepages in your VM image (sudo sh -c "echo always > /sys/kernel/mm/transparent_hugepage/enabled")
  warnings.warn(


In [ ]:
#GENEL TEST FONKSİYONU ÇALIŞTIRILACAK
import numpy as np
from sklearn.metrics import accuracy_score, precision_score, recall_score, f1_score
import tensorflow as tf

def TestSonuclari(test_ds,model_nn,client_name):
  # Test etiketlerini ve ID'leri al
  test_labels = np.array(list(test_ds.map(lambda x, y: y).unbatch().as_numpy_iterator()))

  # Model tahminlerini al (binary sınıflandırma için 0.5 eşik)
  pred_probs = model_nn.predict(test_ds)
  pred_labels = (pred_probs.flatten() > 0.5).astype(int)

  # Test kaybını model üzerinden de alabilirsin (model.evaluate ile)
  results = model_nn.evaluate(test_ds, verbose=0)
  # F1 Score Calculation
  if results[2] + results[3] == 0:
      f1_score = 0.0
  else:
      f1_score = 2 * (results[2] * results[3]) / (results[2] + results[3])
  print(f"{client_name} Loss: {results[0]:.4f}")
  print(f"{client_name} Accuracy: {results[1]:.4f}")
  print(f"{client_name} Precision: {results[2]:.4f}")
  print(f"{client_name} Recall: {results[3]:.4f}")
  print(f"{client_name} F1-Score: {f1_score:.4f}")

In [ ]:
import numpy as np
from collections import Counter
from sklearn.metrics import accuracy_score, precision_score, recall_score, f1_score, confusion_matrix, classification_report
from tensorflow.keras.losses import BinaryCrossentropy

def TestSonuclariFedCycle_robust(test_ds, model_nn, client_name, debug_batches=3):
    # 1) Iterate over dataset batch-by-batch, collect labels and predictions robustly
    labels = []
    preds = []
    sample_count = 0
    first_debug = True

    for batch_i, batch in enumerate(test_ds):
        try:
            x_batch, y_batch = batch
        except Exception:
            # If dataset yields tuple differently, try unpack via tf.nest
            x_batch = batch[0]
            y_batch = batch[1]

        # Debug: print shapes/types for first few batches
        if batch_i < debug_batches:
            try:
                print(f"[DEBUG] batch {batch_i}: x.shape={getattr(x_batch, 'shape', None)} dtype={getattr(x_batch, 'dtype', None)}, y.shape={getattr(y_batch, 'shape', None)} dtype={getattr(y_batch, 'dtype', None)}")
            except Exception as e:
                print("[DEBUG] could not print batch shapes:", e)

        # Normalize y_batch -> ensure shape (batch,) and int
        # Use tf.squeeze then convert to numpy
        try:
            # in eager mode y_batch.numpy() should work
            y_np = np.array(y_batch)  # handles e.g. (batch,1) or (batch,) or scalar broadcast
            y_np = np.squeeze(y_np)   # shape could become (,) for batch_size=1 or (batch_size,)
            # If after squeeze we still have scalar (this happens when batch_size==1), make it 1d
            if y_np.ndim == 0:
                y_list = [int(y_np)]
            else:
                y_list = [int(v) for v in y_np.tolist()]
        except Exception as e:
            # fallback: try iterating elements
            y_list = []
            try:
                for yi in tf.unstack(tf.convert_to_tensor(y_batch)):
                    y_list.append(int(np.array(yi).squeeze()))
            except Exception as e2:
                raise RuntimeError(f"Cannot normalize labels in batch {batch_i}: {e}; fallback error: {e2}")

        labels.extend(y_list)
        sample_count += len(y_list)

        # Predictions for this batch (use model call rather than predict to avoid internal vectorization issues)
        try:
            preds_batch = model_nn(x_batch, training=False)
            preds_batch = np.array(preds_batch)  # convert to numpy array
            # If output shape is (batch,1) flatten to (batch,)
            preds_batch = preds_batch.reshape((preds_batch.shape[0], -1))
            if preds_batch.shape[1] == 1:
                preds_flat = preds_batch[:,0]
            else:
                # if model outputs (batch,2) probabilities, take prob for class 1
                if preds_batch.shape[1] == 2:
                    preds_flat = preds_batch[:,1]
                else:
                    # fallback: flatten entire row (shouldn't usually happen)
                    preds_flat = preds_batch[:,0]
            preds.extend(preds_flat.tolist())
        except Exception as e:
            print(f"[ERROR] model inference failed on batch {batch_i}: {e}")
            # Try predict_on_batch as fallback
            try:
                preds_batch = model_nn.predict_on_batch(x_batch)
                preds_batch = np.array(preds_batch).reshape((preds_batch.shape[0], -1))
                if preds_batch.shape[1] == 1:
                    preds_flat = preds_batch[:,0]
                else:
                    preds_flat = preds_batch[:,1] if preds_batch.shape[1] == 2 else preds_batch[:,0]
                preds.extend(preds_flat.tolist())
            except Exception as e2:
                raise RuntimeError(f"Both direct call and predict_on_batch failed for batch {batch_i}: {e2}")

    # Convert to numpy arrays
    labels = np.array(labels, dtype=int)
    preds = np.array(preds, dtype=float)

    print(f"Total samples collected: {labels.shape[0]} (should match dataset size)")

    # Convert to binary pred labels using threshold 0.5
    pred_labels = (preds > 0.5).astype(int)

    # 2) Try using model.evaluate (optional). If it fails, we'll rely on sklearn metrics below.
    eval_results = None
    try:
        eval_results = model_nn.evaluate(test_ds, verbose=0)
        print("[INFO] model.evaluate succeeded.")
    except Exception as e:
        print("[WARN] model.evaluate failed, will compute metrics via sklearn. Error:", e)

    # 3) Compute metrics (use sklearn for reliability)
    acc = accuracy_score(labels, pred_labels)
    prec = precision_score(labels, pred_labels, zero_division=0)
    rec = recall_score(labels, pred_labels, zero_division=0)
    f1 = f1_score(labels, pred_labels, zero_division=0)

    print(f"\n{client_name} (robust) Results:")
    if eval_results is not None:
        # try to print loss/acc from evaluate if available
        loss_v = eval_results[0] if len(eval_results)>0 else float('nan')
        acc_v  = eval_results[1] if len(eval_results)>1 else acc
        print(f"{client_name} Loss (model.evaluate): {loss_v:.4f}")
        print(f"{client_name} Accuracy (model.evaluate): {acc_v:.4f}")
    print(f"{client_name} Accuracy (sklearn): {acc:.4f}")
    print(f"{client_name} Precision (sklearn): {prec:.4f}")
    print(f"{client_name} Recall (sklearn): {rec:.4f}")
    print(f"{client_name} F1-Score (sklearn): {f1:.4f}")

   # sklearn metriclerin hesaplandığı kısımda
    bce = BinaryCrossentropy()
    loss_manual = bce(labels, preds).numpy()

    print(f"{client_name} Loss (manual BCE): {loss_manual:.4f}")
    # Confusion matrix + report
    try:
        print("\nClassification report:\n", classification_report(labels, pred_labels, digits=4))
        print("Confusion matrix:\n", confusion_matrix(labels, pred_labels))
    except Exception as e:
        print("Could not produce classification report/confusion matrix:", e)

    return {
        "n_samples": labels.shape[0],
        "accuracy": acc,
        "precision": prec,
        "recall": rec,
        "f1": f1,
        "preds": preds,
        "labels": labels
    }


In [ ]:
# Şimdi concatenation yapılabilir
import functools
def normalize_labels(dataset):
    return dataset.map(lambda x, y: (x, tf.cast(y, tf.int64)))
def merge_test_datasets(test_RSNA,test_Robo,testBreak_dataset,test_busi,test_bcfpp):
  # Tüm test datasetlerini aynı dtype'a çeviriyoruz
  test_RSNA1   = normalize_labels(test_RSNA)
  test_Robo1   = normalize_labels(test_Robo)
  testBreak_dataset1 = normalize_labels(testBreak_dataset)
  test_busi1   = normalize_labels(test_busi)
  test_bcfpp1  = normalize_labels(test_bcfpp)
  test_datasets = [test_RSNA1, test_Robo1, testBreak_dataset1, test_busi1, test_bcfpp1]
  all_test = functools.reduce(lambda a, b: a.concatenate(b), test_datasets)

  # Eğer batch yoksa burada ekle
  first_elem = next(iter(all_test))
  if len(first_elem[0].shape) == 3:  # (224,224,3) -> unbatched
      all_test = all_test.batch(32)
  # Eğer zaten batch varsa, direkt devam et

  all_test = all_test.map(
      lambda x, y: (x, tf.reshape(y, [-1]))
  ).prefetch(tf.data.AUTOTUNE)
  return all_test


In [ ]:
#RSNA VERİ SETİ YÜKLEME & EĞİTME ÇALIŞTIRILACAK
path = kagglehub.dataset_download("gauravduttakiit/rsna-screening-mammography-breast-cancer-detection")
train_RSNA, val_RSNA,test_RSNA, test_data=load_rsna_data(path)
#sayılar
train_sample_count = sum(1 for _ in train_RSNA.unbatch())
val_sample_count = sum(1 for _ in val_RSNA.unbatch())
test_sample_count = sum(1 for _ in test_RSNA.unbatch())
# Gerçek etiketleri sırayla al
test_RSNAlabels = np.array(list(test_RSNA.map(lambda x, y: y).unbatch().as_numpy_iterator()))

print(f"RSNA Train samples: {train_sample_count}")
print(f"RSNA Validation samples: {val_sample_count}")
print(f"Test samples (kesin): {test_sample_count}")

Using Colab cache for faster access to the 'rsna-screening-mammography-breast-cancer-detection' dataset.
RSNA Train samples: 5191
RSNA Validation samples: 2196
Test samples (kesin): 1098


In [ ]:
#ROBOFLOW LOADING ÇALIŞTIRILACAK
import tensorflow as tf
# Download latest version
path_ds = kagglehub.dataset_download("hayder17/breast-cancer-detection")
train_Robo, val_Robo,test_Robo=load_roboflow_data(path_ds)
#sayılar
train_sample_count = sum(1 for _ in train_Robo.unbatch())
val_sample_count = sum(1 for _ in val_Robo.unbatch())
test_sample_count = sum(1 for _ in test_Robo.unbatch())

# Gerçek etiketleri sırayla al
test_Robolabels = np.array(list(test_Robo.map(lambda x, y: y).unbatch().as_numpy_iterator()))

print(f"Roboflow Train samples: {train_sample_count}")
print(f"Roboflow Validation samples: {val_sample_count}")
print(f"Roboflow Validation samples: {test_sample_count}")

Using Colab cache for faster access to the 'breast-cancer-detection' dataset.
Roboflow Train samples: 2134
Roboflow Validation samples: 675
Roboflow Validation samples: 238


In [ ]:
#BREAKHIS LOADING ÇALIŞTIRILACAK
# %%
from functools import partial

# BreakHis veri kümesinin yolunu belirleyelim
# Download latest version
path = kagglehub.dataset_download("ambarish/breakhis")
trainBreak_dataset,valBreak_dataset,testBreak_dataset=load_breakhis_data(path)
print("Train veri seti örnek sayısı:", trainBreak_dataset.cardinality().numpy())
print("Validation veri seti örnek sayısı:", valBreak_dataset.cardinality().numpy())
print("Test veri seti örnek sayısı:", testBreak_dataset.cardinality().numpy())


# Gerçek etiketleri sırayla al
test_Breaklabels = np.array(list(testBreak_dataset.map(lambda x, y: y).unbatch().as_numpy_iterator()))

Using Colab cache for faster access to the 'breakhis' dataset.
Train veri seti örnek sayısı: 1227
Validation veri seti örnek sayısı: 223
Test veri seti örnek sayısı: 124


In [ ]:
#BUSI VERİ SETİ LOADING ÇALIŞTIRILACAK
import os
import tensorflow as tf
from sklearn.model_selection import train_test_split
import kagglehub
#https://www.kaggle.com/datasets/sabahesaraki/breast-ultrasound-images-dataset/data
# Download latest version
path = kagglehub.dataset_download("sabahesaraki/breast-ultrasound-images-dataset")
train_busi, val_busi, test_busi = load_busi_data(path)
#sayılar
train_sample_count = sum(1 for _ in train_busi.unbatch())
val_sample_count = sum(1 for _ in val_busi.unbatch())
test_sample_count = sum(1 for _ in test_busi.unbatch())


print(f"BUSI Train samples: {train_sample_count}")
print(f"BUSI Validation samples: {val_sample_count}")
print(f"BUSI Test samples: {test_sample_count}")

# Gerçek etiketleri sırayla al
test_Busilabels = np.array(list(test_busi.map(lambda x, y: y).unbatch().as_numpy_iterator()))

Using Colab cache for faster access to the 'breast-ultrasound-images-dataset' dataset.
BUSI Train samples: 561
BUSI Validation samples: 141
BUSI Test samples: 78


In [ ]:
#BCFPP LOADING ÇALIŞTIRILACAK
import os
import tensorflow as tf
from sklearn.model_selection import train_test_split
import kagglehub
import joblib as jlb

path = kagglehub.dataset_download("sabermalek/bcfpp")
jlb_path = os.path.join(path, "BCFPP.jlb")
data = jlb.load(jlb_path)
train_bcfpp, val_bcfpp, test_bcfpp = load_bcfpp_data(jlb_path,data)
#görüntüler zaten numpy array olduğu için preprocess yapmıyoruz
#sayılar
train_sample_count = sum(1 for _ in train_bcfpp.unbatch())
val_sample_count = sum(1 for _ in val_bcfpp.unbatch())
test_sample_count = sum(1 for _ in test_bcfpp.unbatch())


print(f"BCFPP Train samples: {train_sample_count}")
print(f"BCFPP Validation samples: {val_sample_count}")
print(f"BCFPP Test samples: {test_sample_count}")

# Gerçek etiketleri sırayla al
test_BCFlabels = np.array(list(test_bcfpp.map(lambda x, y: y).unbatch().as_numpy_iterator()))

Using Colab cache for faster access to the 'bcfpp' dataset.
BCFPP Train samples: 2592
BCFPP Validation samples: 648
BCFPP Test samples: 360


In [ ]:
client_images = [trainBreak_dataset, train_busi, train_Robo,train_RSNA,train_bcfpp]
val_images= [valBreak_dataset, val_busi, val_Robo,val_RSNA,val_bcfpp]
test_images =[testBreak_dataset,test_busi,test_Robo,test_RSNA,test_bcfpp]
test_labels=[test_Breaklabels,test_Busilabels,test_Robolabels,test_RSNAlabels,test_BCFlabels]

In [ ]:
def merge_histories(history_list):
  merged = {}
  for h in history_list:
      for k, v in h.history.items():
          if k not in merged:
              merged[k] = []
          merged[k].extend(v)  # değerleri listeye ekle
  return merged

In [ ]:
#EFFICIENTB0 19787 gibi zaman sürdü
model_handle="https://tfhub.dev/google/imagenet/efficientnet_v2_b0/feature_vector/1"
# Model checkpoint ve log ayarları
model_checkpoint = ModelCheckpoint('FLEffB0.weights.h5', save_best_only=True, save_weights_only=True)
csv_logger = CSVLogger('FLEffB0Logs.csv', append=True)
client_name=["Breakhis","Busi","Roboflow","Rsna","Bcfpp"]
#global model
IMG_SIZE =224
global_model = make_nn_model_efficientb0(IMG_SIZE,trainb=True)
# Başlangıç global modeli: ilk client eğitiminden önce oluşturulsun
global_model.compile(optimizer=AdamW(learning_rate=1e-3, weight_decay=1e-4),
                      loss='binary_crossentropy',
                      metrics=['accuracy', Precision(name='precision'), Recall(name='recall')])
total_samples=0
#deneme
for idx, cname in enumerate(client_name):
    n_client = tf.data.experimental.cardinality(client_images[idx]).numpy()
    n_client *= 32
    print(f"{cname} n_client: {n_client}")
#


In [ ]:
#fit model
start = time.time()
#ilki client 1 ve global model oluşturuluyor
global_model,total_samples,train_history = train_fedcycle_model(model_handle, client_images, val_images,test_images, test_labels, model_checkpoint,csv_logger,"EFFB0",total_samples,global_model,epochs=10)

end = time.time()
print('Time Taken: %.3f seconds' % (end-start))

In [ ]:
TestSonuclari(testBreak_dataset,global_model,"Break Test")
TestSonuclari(test_busi,global_model,"Busi Test")
TestSonuclari(test_RSNA,global_model,"Rsna Test")
TestSonuclari(test_Robo,global_model,"Robo Test")
TestSonuclari(test_bcfpp,global_model,"Bcfpp Test")

In [ ]:
all_tests=merge_test_datasets(test_RSNA,test_Robo,testBreak_dataset,test_busi,test_bcfpp)
TestSonuclariFedCycle_robust(all_tests,global_model,"FEDCYCLE_EFFICIENT")

In [ ]:
#MOBILE
# Model checkpoint ve log ayarları
model_handle=""
model_checkpoint = ModelCheckpoint('FLMobile.weights.h5', save_best_only=True, save_weights_only=True)
csv_logger = CSVLogger('FLMobileLogs.csv', append=True)
#global model
IMG_SIZE =224
global_model = make_nn_model_mobileNet(IMG_SIZE,trainb=True)
# Başlangıç global modeli: ilk client eğitiminden önce oluşturulsun
global_model.compile(optimizer=AdamW(learning_rate=1e-3, weight_decay=1e-4),
                      loss='binary_crossentropy',
                      metrics=['accuracy', Precision(name='precision'), Recall(name='recall')])
total_samples=0
#fit model
start = time.time()
#ilki client 1 ve global model oluşturuluyor
global_model,total_samples,train_history = train_fedcycle_model(model_handle, client_images, val_images,test_images, test_labels, model_checkpoint,csv_logger,"MOBILE",total_samples,global_model,epochs=10)

end = time.time()
print('Time Taken: %.3f seconds' % (end-start))

In [ ]:
TestSonuclari(testBreak_dataset,global_model,"Break Test")
TestSonuclari(test_busi,global_model,"Busi Test")
TestSonuclari(test_RSNA,global_model,"Rsna Test")
TestSonuclari(test_Robo,global_model,"Robo Test")
TestSonuclari(test_bcfpp,global_model,"Bcfpp Test")

In [ ]:
all_tests=merge_test_datasets(test_RSNA,test_Robo,testBreak_dataset,test_busi,test_bcfpp)
TestSonuclariFedCycle_robust(all_tests,global_model,"FEDCYCLE_MOBILE")

In [ ]:
#MOBILEV3
# Model checkpoint ve log ayarları
from modelbuilder import make_nn_model_mobileNetV3
model_handle=""
model_checkpoint = ModelCheckpoint('FLMobile.weights.h5', save_best_only=True, save_weights_only=True)
csv_logger = CSVLogger('FLMobileLogs.csv', append=True)
client_name=["Breakhis","Busi","Roboflow","Rsna","Bcfpp"]
#global model
IMG_SIZE =224
global_model = make_nn_model_mobileNetV3(IMG_SIZE,trainb=True)
# Başlangıç global modeli: ilk client eğitiminden önce oluşturulsun
global_model.compile(optimizer=AdamW(learning_rate=1e-3, weight_decay=1e-4),
                      loss='binary_crossentropy',
                      metrics=['accuracy', Precision(name='precision'), Recall(name='recall')])
total_samples=0
#fit model
start = time.time()
#ilki client 1 ve global model oluşturuluyor
global_model,total_samples,train_history = train_fedcycle_model(model_handle, client_images, val_images,test_images, test_labels, model_checkpoint,csv_logger,"MOBV3",total_samples,global_model,epochs=10)

end = time.time()
print('Time Taken: %.3f seconds' % (end-start))

In [ ]:
TestSonuclari(testBreak_dataset,global_model,"Break Test")
TestSonuclari(test_busi,global_model,"Busi Test")
TestSonuclari(test_RSNA,global_model,"Rsna Test")
TestSonuclari(test_Robo,global_model,"Robo Test")
TestSonuclari(test_bcfpp,global_model,"Bcfpp Test")

In [ ]:
all_tests=merge_test_datasets(test_RSNA,test_Robo,testBreak_dataset,test_busi,test_bcfpp)
TestSonuclariFedCycle_robust(all_tests,global_model,"FED_WEIGHT_MOBILEV3")

In [ ]:
#EFFICIENTB7
# Model checkpoint ve log ayarları
model_handle=""
model_checkpoint = ModelCheckpoint('EFFB7.weights.h5', save_best_only=True, save_weights_only=True)
csv_logger = CSVLogger('EFFB7Logs.csv', append=True)
#global model
IMG_SIZE =224
global_model = make_nn_model_efficientb7(IMG_SIZE,trainb=True)
# Başlangıç global modeli: ilk client eğitiminden önce oluşturulsun
global_model.compile(optimizer=AdamW(learning_rate=1e-3, weight_decay=1e-4),
                      loss='binary_crossentropy',
                      metrics=['accuracy', Precision(name='precision'), Recall(name='recall')])
total_samples=0
#fit model
start = time.time()
#ilki client 1 ve global model oluşturuluyor
global_model,total_samples,train_history = train_fedcycle_model(model_handle, client_images, val_images,test_images, test_labels, model_checkpoint,csv_logger,"EFFB7",total_samples,global_model,epochs=10)

end = time.time()
print('Time Taken: %.3f seconds' % (end-start))

Making our deep cnn model EFFICIENT B6.....
165234480/165234480 ━━━━━━━━━━━━━━━━━━━━ 1s 0us/step


Model: "efficientb6_model"

┏━━━━━━━━━━━━━━━━━━━━━┳━━━━━━━━━━━━━━━━━━━┳━━━━━━━━━━━━┳━━━━━━━━━━━━━━━━━━━┓
┃ Layer (type)        ┃ Output Shape      ┃    Param # ┃ Connected to      ┃
┡━━━━━━━━━━━━━━━━━━━━━╇━━━━━━━━━━━━━━━━━━━╇━━━━━━━━━━━━╇━━━━━━━━━━━━━━━━━━━┩
│ input_layer         │ (None, 224, 224,  │          0 │ -                 │
│ (InputLayer)        │ 3)                │            │                   │
├─────────────────────┼───────────────────┼────────────┼───────────────────┤
│ rescaling           │ (None, 224, 224,  │          0 │ input_layer[0][0] │
│ (Rescaling)         │ 3)                │            │                   │
├─────────────────────┼───────────────────┼────────────┼───────────────────┤
│ normalization       │ (None, 224, 224,  │          7 │ rescaling[0][0]   │
│ (Normalization)     │ 3)                │            │                   │
├─────────────────────┼───────────────────┼────────────┼───────────────────┤
│ rescaling_1         │ (None, 224, 224,  │          0 │ normalization[0]… │
│ (Rescaling)         │ 3)                │            │                   │
├─────────────────────┼───────────────────┼────────────┼───────────────────┤
│ stem_conv_pad       │ (None, 225, 225,  │          0 │ rescaling_1[0][0] │
│ (ZeroPadding2D)     │ 3)                │            │                   │
├─────────────────────┼───────────────────┼────────────┼───────────────────┤
│ stem_conv (Conv2D)  │ (None, 112, 112,  │      1,512 │ stem_conv_pad[0]… │
│                     │ 56)               │            │                   │
├─────────────────────┼───────────────────┼────────────┼───────────────────┤
│ stem_bn             │ (None, 112, 112,  │        224 │ stem_conv[0][0]   │
│ (BatchNormalizatio… │ 56)               │            │                   │
├─────────────────────┼───────────────────┼────────────┼───────────────────┤
│ stem_activation     │ (None, 112, 112,  │          0 │ stem_bn[0][0]     │
│ (Activation)        │ 56)               │            │                   │
├─────────────────────┼───────────────────┼────────────┼───────────────────┤
│ block1a_dwconv      │ (None, 112, 112,  │        504 │ stem_activation[… │
│ (DepthwiseConv2D)   │ 56)               │            │                   │
├─────────────────────┼───────────────────┼────────────┼───────────────────┤
│ block1a_bn          │ (None, 112, 112,  │        224 │ block1a_dwconv[0… │
│ (BatchNormalizatio… │ 56)               │            │                   │
├─────────────────────┼───────────────────┼────────────┼───────────────────┤
│ block1a_activation  │ (None, 112, 112,  │          0 │ block1a_bn[0][0]  │
│ (Activation)        │ 56)               │            │                   │
├─────────────────────┼───────────────────┼────────────┼───────────────────┤
│ block1a_se_squeeze  │ (None, 56)        │          0 │ block1a_activati… │
│ (GlobalAveragePool… │                   │            │                   │
├─────────────────────┼───────────────────┼────────────┼───────────────────┤
│ block1a_se_reshape  │ (None, 1, 1, 56)  │          0 │ block1a_se_squee… │
│ (Reshape)           │                   │            │                   │
├─────────────────────┼───────────────────┼────────────┼───────────────────┤
│ block1a_se_reduce   │ (None, 1, 1, 14)  │        798 │ block1a_se_resha… │
│ (Conv2D)            │                   │            │                   │
├─────────────────────┼───────────────────┼────────────┼───────────────────┤
│ block1a_se_expand   │ (None, 1, 1, 56)  │        840 │ block1a_se_reduc… │
│ (Conv2D)            │                   │            │                   │
├─────────────────────┼───────────────────┼────────────┼───────────────────┤
│ block1a_se_excite   │ (None, 112, 112,  │          0 │ block1a_activati… │
│ (Multiply)          │ 56)               │            │ block1a_se_expan… │
├─────────────────────┼───────────────────┼────────────┼───────────────────┤
│ block1a_project_co… │ (None, 112, 112,  │      1,792 │ block1a_se_excit

 Total params: 42,208,656 (161.01 MB)

 Trainable params: 41,982,937 (160.15 MB)

...

┏━━━━━━━━━━━━━━━━━━━━━┳━━━━━━━━━━━━━━━━━━━┳━━━━━━━━━━━━┳━━━━━━━━━━━━━━━━━━━┓
┃ Layer (type)        ┃ Output Shape      ┃    Param # ┃ Connected to      ┃
┡━━━━━━━━━━━━━━━━━━━━━╇━━━━━━━━━━━━━━━━━━━╇━━━━━━━━━━━━╇━━━━━━━━━━━━━━━━━━━┩
│ input_layer_5       │ (None, 224, 224,  │          0 │ -                 │
│ (InputLayer)        │ 3)                │            │                   │
├─────────────────────┼───────────────────┼────────────┼───────────────────┤
│ rescaling_10        │ (None, 224, 224,  │          0 │ input_layer_5[0]… │
│ (Rescaling)         │ 3)                │            │                   │
├─────────────────────┼───────────────────┼────────────┼───────────────────┤
│ normalization_5     │ (None, 224, 224,  │          7 │ rescaling_10[0][… │
│ (Normalization)     │ 3)                │            │                   │
├─────────────────────┼───────────────────┼────────────┼───────────────────┤
│ rescaling_11        │ (None, 224, 224,  │          0 │ normalization_5[… │
│ (Rescaling)         │ 3)                │            │                   │
├─────────────────────┼───────────────────┼────────────┼───────────────────┤
│ stem_conv_pad       │ (None, 225, 225,  │          0 │ rescaling_11[0][… │
│ (ZeroPadding2D)     │ 3)                │            │                   │
├─────────────────────┼───────────────────┼────────────┼───────────────────┤
│ stem_conv (Conv2D)  │ (None, 112, 112,  │      1,512 │ stem_conv_pad[0]… │
│                     │ 56)               │            │                   │
├─────────────────────┼───────────────────┼────────────┼───────────────────┤
│ stem_bn             │ (None, 112, 112,  │        224 │ stem_conv[0][0]   │
│ (BatchNormalizatio… │ 56)               │            │                   │
├─────────────────────┼───────────────────┼────────────┼───────────────────┤
│ stem_activation     │ (None, 112, 112,  │          0 │ stem_bn[0][0]     │
│ (Activation)        │ 56)               │            │                   │
├─────────────────────┼───────────────────┼────────────┼───────────────────┤
│ block1a_dwconv      │ (None, 112, 112,  │        504 │ stem_activation[… │
│ (DepthwiseConv2D)   │ 56)               │            │                   │
├─────────────────────┼───────────────────┼────────────┼───────────────────┤
│ block1a_bn          │ (None, 112, 112,  │        224 │ block1a_dwconv[0… │
│ (BatchNormalizatio… │ 56)               │            │                   │
├─────────────────────┼───────────────────┼────────────┼───────────────────┤
│ block1a_activation  │ (None, 112, 112,  │          0 │ block1a_bn[0][0]  │
│ (Activation)        │ 56)               │            │                   │
├─────────────────────┼───────────────────┼────────────┼───────────────────┤
│ block1a_se_squeeze  │ (None, 56)        │          0 │ block1a_activati… │
│ (GlobalAveragePool… │                   │            │                   │
├─────────────────────┼───────────────────┼────────────┼───────────────────┤
│ block1a_se_reshape  │ (None, 1, 1, 56)  │          0 │ block1a_se_squee… │
│ (Reshape)           │                   │            │                   │
├─────────────────────┼───────────────────┼────────────┼───────────────────┤
│ block1a_se_reduce   │ (None, 1, 1, 14)  │        798 │ block1a_se_resha… │
│ (Conv2D)            │                   │            │                   │
├─────────────────────┼───────────────────┼────────────┼───────────────────┤
│ block1a_se_expand   │ (None, 1, 1, 56)  │        840 │ block1a_se_reduc… │
│ (Conv2D)            │                   │            │                   │
├─────────────────────┼───────────────────┼────────────┼───────────────────┤
│ block1a_se_excite   │ (None, 112, 112,  │          0 │ block1a_activati… │
│ (Multiply)          │ 56)               │            │ block1a_se_expan… │
├─────────────────────┼───────────────────┼────────────┼───────────────────┤
│ block1a_project_co… │ (None, 112, 112,  │      1,792 │ block1a_se_excit

 Total params: 42,208,656 (161.01 MB)

 Trainable params: 41,982,937 (160.15 MB)

 Non-trainable params: 225,719 (881.72 KB)

model built!
Epoch 1/50 - FedCycle Training

>>> Breakhis Train Başladı <<<

 110/1227 ━━━━━━━━━━━━━━━━━━━━ 1:50:58 6s/step - accuracy: 0.7814 - loss: 0.4974 - precision: 0.7805 - recall: 0.7941

In [ ]:
TestSonuclari(testBreak_dataset,global_model,"Break Test")
TestSonuclari(test_busi,global_model,"Busi Test")
TestSonuclari(test_RSNA,global_model,"Rsna Test")
TestSonuclari(test_Robo,global_model,"Robo Test")
TestSonuclari(test_bcfpp,global_model,"Bcfpp Test")

In [ ]:
all_tests=merge_test_datasets(test_RSNA,test_Robo,testBreak_dataset,test_busi,test_bcfpp)
TestSonuclariFedCycle_robust(all_tests,global_model,"FEDCYCLE_MOBILEV3")

In [ ]:
#DENSENET ÇALIŞTIRILACAK
# Model checkpoint ve log ayarları
model_handle=""
model_checkpoint = ModelCheckpoint('DENSE.weights.h5', save_best_only=True, save_weights_only=True)
csv_logger = CSVLogger('DENSELogs.csv', append=True)
#global model
IMG_SIZE =224
global_model = make_nn_model_dense(IMG_SIZE,trainb=True)
# Başlangıç global modeli: ilk client eğitiminden önce oluşturulsun
global_model.compile(optimizer=AdamW(learning_rate=1e-3, weight_decay=1e-4),
                      loss='binary_crossentropy',
                      metrics=['accuracy', Precision(name='precision'), Recall(name='recall')])
total_samples=0
#fit model
start = time.time()
#ilki client 1 ve global model oluşturuluyor
#ilki client 1 ve global model oluşturuluyor
global_model,total_samples,train_history = train_fedcycle_model(model_handle, client_images, val_images,test_images, test_labels, model_checkpoint,csv_logger,"DENSE",total_samples,global_model,epochs=10)

end = time.time()
print('Time Taken: %.3f seconds' % (end-start))

Making DenseNet201 model...


Model: "functional_2"

┏━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━┳━━━━━━━━━━━━━━━━━━━━━━━━┳━━━━━━━━━━━━━━━┓
┃ Layer (type)                    ┃ Output Shape           ┃       Param # ┃
┡━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━╇━━━━━━━━━━━━━━━━━━━━━━━━╇━━━━━━━━━━━━━━━┩
│ input_layer_5 (InputLayer)      │ (None, 224, 224, 3)    │             0 │
├─────────────────────────────────┼────────────────────────┼───────────────┤
│ base (Functional)               │ (None, 1920)           │    18,321,984 │
├─────────────────────────────────┼────────────────────────┼───────────────┤
│ dense_6 (Dense)                 │ (None, 512)            │       983,552 │
├─────────────────────────────────┼────────────────────────┼───────────────┤
│ batch_normalization_4           │ (None, 512)            │         2,048 │
│ (BatchNormalization)            │                        │               │
├─────────────────────────────────┼────────────────────────┼───────────────┤
│ dropout_2 (Dropout)             │ (None, 512)            │             0 │
├─────────────────────────────────┼────────────────────────┼───────────────┤
│ dense_7 (Dense)                 │ (None, 128)            │        65,664 │
├─────────────────────────────────┼────────────────────────┼───────────────┤
│ batch_normalization_5           │ (None, 128)            │           512 │
│ (BatchNormalization)            │                        │               │
├─────────────────────────────────┼────────────────────────┼───────────────┤
│ dense_8 (Dense)                 │ (None, 1)              │           129 │
└─────────────────────────────────┴────────────────────────┴───────────────┘

 Total params: 19,373,889 (73.91 MB)

 Trainable params: 19,143,553 (73.03 MB)

...

┏━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━┳━━━━━━━━━━━━━━━━━━━━━━━━┳━━━━━━━━━━━━━━━┓
┃ Layer (type)                    ┃ Output Shape           ┃       Param # ┃
┡━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━╇━━━━━━━━━━━━━━━━━━━━━━━━╇━━━━━━━━━━━━━━━┩
│ input_layer_15 (InputLayer)     │ (None, 224, 224, 3)    │             0 │
├─────────────────────────────────┼────────────────────────┼───────────────┤
│ base (Functional)               │ (None, 1920)           │    18,321,984 │
├─────────────────────────────────┼────────────────────────┼───────────────┤
│ dense_21 (Dense)                │ (None, 512)            │       983,552 │
├─────────────────────────────────┼────────────────────────┼───────────────┤
│ batch_normalization_14          │ (None, 512)            │         2,048 │
│ (BatchNormalization)            │                        │               │
├─────────────────────────────────┼────────────────────────┼───────────────┤
│ dropout_7 (Dropout)             │ (None, 512)            │             0 │
├─────────────────────────────────┼────────────────────────┼───────────────┤
│ dense_22 (Dense)                │ (None, 128)            │        65,664 │
├─────────────────────────────────┼────────────────────────┼───────────────┤
│ batch_normalization_15          │ (None, 128)            │           512 │
│ (BatchNormalization)            │                        │               │
├─────────────────────────────────┼────────────────────────┼───────────────┤
│ dense_23 (Dense)                │ (None, 1)              │           129 │
└─────────────────────────────────┴────────────────────────┴───────────────┘

 Total params: 19,373,889 (73.91 MB)

 Trainable params: 19,143,553 (73.03 MB)

 Non-trainable params: 230,336 (899.75 KB)


>>> BCFPP Dataset Train Starts <<<

Epoch 1/70
81/81 ━━━━━━━━━━━━━━━━━━━━ 0s 1s/step - accuracy: 0.6142 - loss: 2.1416 - precision: 0.4257 - recall: 0.6437Epoch 1: Train F1-score = 0.5282, Val F1-score = 0.0000
Epoch 1: Test Loss = 0.8784, Test Accuracy = 0.6611
81/81 ━━━━━━━━━━━━━━━━━━━━ 158s 2s/step - accuracy: 0.6143 - loss: 2.1318 - precision: 0.4261 - recall: 0.6435 - val_accuracy: 0.6620 - val_loss: 0.8717 - val_precision: 0.0000e+00 - val_recall: 0.0000e+00 - learning_rate: 0.0010 - f1_score: 0.5282 - val_f1_score: 0.0000e+00 - test_accuracy: 0.6611 - test_loss: 0.8784
Epoch 2/70
81/81 ━━━━━━━━━━━━━━━━━━━━ 0s 1s/step - accuracy: 0.7491 - loss: 0.5190 - precision: 0.6168 - recall: 0.6377Epoch 2: Train F1-score = 0.6136, Val F1-score = 0.0091
Epoch 2: Test Loss = 0.6829, Test Accuracy = 0.6667
81/81 ━━━━━━━━━━━━━━━━━━━━ 124s 2s/step - accuracy: 0.7491 - loss: 0.5189 - precision: 0.6170 - recall: 0.6372 - val_accuracy: 0.6651 - val_loss: 0.7152 - val_precision: 0.3333 - val_recall

In [ ]:
#ÇALIŞTIRILACAK
TestSonuclari(testBreak_dataset,global_model,"Break Test")
TestSonuclari(test_busi,global_model,"Busi Test")
TestSonuclari(test_RSNA,global_model,"Rsna Test")
TestSonuclari(test_Robo,global_model,"Robo Test")
TestSonuclari(test_bcfpp,global_model,"Bcfpp Test")

In [ ]:
all_tests=merge_test_datasets(test_RSNA,test_Robo,testBreak_dataset,test_busi,test_bcfpp)
TestSonuclariFedCycle_robust(all_tests,global_model,"FEDCYCLE_DENSENET")

In [ ]:
#RESTNETV2
# Model checkpoint ve log ayarları
model_handle=""
model_checkpoint = ModelCheckpoint('REST.weights.h5', save_best_only=True, save_weights_only=True)
csv_logger = CSVLogger('RESTLogs.csv', append=True)
#global model
IMG_SIZE =224
global_model = make_nn_model_resnet152(IMG_SIZE,trainb=True)
# Başlangıç global modeli: ilk client eğitiminden önce oluşturulsun
global_model.compile(optimizer=AdamW(learning_rate=1e-3, weight_decay=1e-4),
                      loss='binary_crossentropy',
                      metrics=['accuracy', Precision(name='precision'), Recall(name='recall')])
total_samples=0
#fit model
start = time.time()
#ilki client 1 ve global model oluşturuluyor
#ilki client 1 ve global model oluşturuluyor
global_model,total_samples,train_history = train_fedcycle_model(model_handle, client_images, val_images,test_images, test_labels, model_checkpoint,csv_logger,"RESTNET",total_samples,global_model,epochs=10)

end = time.time()
print('Time Taken: %.3f seconds' % (end-start))

In [ ]:
TestSonuclari(testBreak_dataset,global_model,"Break Test")
TestSonuclari(test_busi,global_model,"Busi Test")
TestSonuclari(test_RSNA,global_model,"Rsna Test")
TestSonuclari(test_Robo,global_model,"Robo Test")
TestSonuclari(test_bcfpp,global_model,"Bcfpp Test")

In [ ]:
all_tests=merge_test_datasets(test_RSNA,test_Robo,testBreak_dataset,test_busi,test_bcfpp)
TestSonuclariFedCycle_robust(all_tests,global_model,"FEDCYCLE_RESNET")